### Imports

In [1]:
import struct
import os
from scipy.optimize import curve_fit
from mpl_toolkits.mplot3d import Axes3D
import plotly.io as pio # themes
import plotly.graph_objects as go
import plotly.express as px
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns; sns.set()
import numpy as np
import pandas as pd

idx = pd.IndexSlice
bgcolour = "rgb(15, 23, 42)"
plotly_template = pio.templates["plotly_dark"]

### Reading & unpacking the binary data file

This code first constructs the path to the out folder for the specific simulation run. It then uses os.listdir to get a list of filenames in the out folder, and filters the list to only include filenames that end with ".bin". The resulting list of snapshot filenames is then sorted, so that the snapshots are processed in order.

In [2]:
simulation_run_folder = "2023-02-13--17-19-58"# "2023-02-12--16-00-00"
snapshot_folder = os.path.join("out", simulation_run_folder)

snapshot_filenames = []
for filename in os.listdir(snapshot_folder):
    if filename.endswith(".bin"):
        snapshot_filenames.append(os.path.join(snapshot_folder, filename))

snapshot_filenames.sort()

#### - Reading the header data

This function reads the header data from the binary file - in most cases, we only need to read the first snapshot, since the header data is the same for all snapshots. 

In [3]:
def read_header(filename):
    with open(filename, 'rb') as f:
        header_dtype = np.dtype([('N', np.int32),
                                ('timestep', np.float32),
                                ('softening_factor', np.float32),
                                ('total_iterations', np.int32),
                                ('snapshot_interval', np.int32),])
        
        header = np.frombuffer(f.read(header_dtype.itemsize), header_dtype)

    n_bodies = header['N'][0]
    timestep = header['timestep'][0]
    softening_factor = header['softening_factor'][0]
    total_iterations = header['total_iterations'][0]
    snapshot_interval = header['snapshot_interval'][0]
    total_snapshots = len(snapshot_filenames) # (total_iterations // snapshot_interval)

    return n_bodies, timestep, softening_factor, total_iterations, snapshot_interval, total_snapshots

Now, we extract the header data and store them in their own variables.

In [4]:
n_bodies, timestep, softening_factor, total_iterations, snapshot_interval, total_snapshots = read_header(snapshot_filenames[0])

print("N: ", n_bodies)
print("timestep: ", timestep, "days")
print("total_iterations: ", total_iterations)
print("snapshot_interval: ", snapshot_interval)
print("softening_factor: ", softening_factor)
print("total_snapshots: ", total_snapshots)

N:  10
timestep:  100.0 days
total_iterations:  1000000
snapshot_interval:  10000
softening_factor:  0.000125
total_snapshots:  100


#### - Reading the snapshot data

This function reads each binary snapshot file in turn using `np.frombuffer`, and returns the data as a numpy array.

In [5]:
def read_snapshots():

    mass = np.zeros((total_iterations, n_bodies), dtype=np.float32)
    pos = np.zeros((total_iterations, n_bodies, 3), dtype=np.float32)
    vel = np.zeros((total_iterations, n_bodies, 3), dtype=np.float32)
    acc = np.zeros((total_iterations, n_bodies, 3), dtype=np.float32)

    dt_bytes = n_bodies * 10 * 4
    iteration = 0

    for snapshot_filename in snapshot_filenames:
        with open(snapshot_filename, "rb") as f:
            f.seek(5 * 4) # Skip the header (20 bytes)

            for i in range(0, snapshot_interval):
                # Read the binary data into a numpy array
                snapshot = np.frombuffer(f.read(dt_bytes), dtype=np.float32)
                
                # Reshape the array to the correct dimensions
                snapshot = snapshot.reshape((n_bodies, 10))

                # Extract the mass, position (x, y, z), velocity (x, y, z), and force (x, y, z) at current timestep
                mass[iteration, :] = snapshot[:, 0]
                pos[iteration, :, :] = snapshot[:, 1:4]
                vel[iteration, :, :] = snapshot[:, 4:7]
                acc[iteration, :, :] = snapshot[:, 7:10]

                iteration += 1

    return mass, pos, vel, acc

#### - Data extraction guide

- mass => `mass[i, :]`   - mass of each particle in the snapshot
- pos  => `pos[i, :, :]` - position of each particle in the snapshot
    - x => `pos[i, :, 0]` - x position
    - y => `pos[i, :, 1]` - y position
    - z => `pos[i, :, 2]` - z position
- vel  => `vel[i, :, :]` - velocity of each particle in the snapshot
    - vx => `vel[i, :, 0]` - x velocity
    - vy => `vel[i, :, 1]` - y velocity
    - vz => `vel[i, :, 2]` - z velocity
- acc  => `acc[i, :, :]` - acceleration of each particle in the snapshot
    - ax => `acc[i, :, 0]` - x acceleration
    - ay => `acc[i, :, 1]` - y acceleration
    - az => `acc[i, :, 2]` - z acceleration

... except data manipulation is easier and faster if we pack the data into a dataframe, so we'll do that instead.

Extracting data into individual dataframes

In [6]:
mass, pos, vel, acc = read_snapshots()

x = pos[:, :, 0]
y = pos[:, :, 1]
z = pos[:, :, 2]
vx = vel[:, :, 0]
vy = vel[:, :, 1]
vz = vel[:, :, 2]
fx = acc[:, :, 0]
fy = acc[:, :, 1]
fz = acc[:, :, 2]

df_list = []
for i in range(n_bodies):
    data = {
        "mass": mass[:, i],
        "x": x[:, i],
        "y": y[:, i],
        "z": z[:, i],
        "vx": vx[:, i],
        "vy": vy[:, i],
        "vz": vz[:, i],
        "fx": fx[:, i],
        "fy": fy[:, i],
        "fz": fz[:, i],
    }
    df_list.append(pd.DataFrame(data))

df = pd.concat(df_list, axis=1, keys=["{}".format(i) for i in range(n_bodies)])

mass = df.loc[:,idx[:,'mass']]
x = df.loc[:,idx[:,'x']] # .groupby(level=0, axis=1).sum()
y = df.loc[:,idx[:,'y']]
z = df.loc[:,idx[:,'z']]

fx = df.loc[:,idx[:,'fx']]
fy = df.loc[:,idx[:,'fy']]
fz = df.loc[:,idx[:,'fz']]

vx = df.loc[:,idx[:,'vx']]
vy = df.loc[:,idx[:,'vy']]
vz = df.loc[:,idx[:,'vz']]

### Plotting the data

In [7]:
# Dataset
iteration_step = 1000
data=[go.Scatter3d( x=df.loc[::iteration_step, idx[f'{i}', 'x']], # this only retrieves every iteration_step'th row
                    y=df.loc[::iteration_step, idx[f'{i}', 'y']], 
                    z=df.loc[::iteration_step, idx[f'{i}', 'z']],
                    mode='lines',
                    name=f'Body {i}',
                    line=dict(
                        width=2*df[f'{i}']['mass'][0],
                        colorscale='Viridis'
                        ))
                    # line=dict(width=2*df[f'{i}']['mass'][0], color='blue'))
                    for i in range(n_bodies)]


# Layout
zoom = 1.2
axis_range = 10000
slider_step=50

layout = go.Layout(
    title='N-Body Simulation',
    autosize=False,
    height=900,
    width=1400,
    template=plotly_template,
    scene=dict(
        aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom),
        xaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        yaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        zaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
    ),
)

fig = go.Figure(data=data, layout=layout)

fig.show()

# import plotly.offline as plotoff
# plotoff.plot(fig, filename='nbody.html')
# pio.write_html(fig, file='nbody.html', auto_open=True)

# testing

In [17]:
iteration_step = 10000

data = []
for t in range(0, df.index[-1]+1, iteration_step):
    frame = go.Scatter3d(x=[], y=[], z=[], mode='lines')
    for i in range(n_bodies):
        frame.x.append(df.loc[t, idx[f'{i}', 'x']])
        frame.y.append(df.loc[t, idx[f'{i}', 'y']])
        frame.z.append(df.loc[t, idx[f'{i}', 'z']])
        frame.line.width.append(2 * df[f'{i}']['mass'][0])
    data.append(frame)

# Layout
zoom = 1.2
axis_range = 10000
layout = go.Layout(
    title='N-Body Simulation',
    autosize=False,
    height=900,
    width=1400,
    scene=dict(
        aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom),
        xaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        yaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        zaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
    ),
    updatemenus=[
        dict(
            type='buttons',
            showactive=False,
            buttons=[
                dict(
                    label='Play',
                    method='animate',
                    args=[None, dict(frame=dict(duration=50, redraw=False),
                                     fromcurrent=True,
                                     transition=dict(duration=0),
                                     mode='immediate'
                                     )
                          ]
                ),
                dict(
                    label='Pause',
                    method='animate',
                    args=[[None], dict(mode='immediate',
                                       transition=dict(duration=0),
                                       frame=dict(duration=0, redraw=False),
                                       mode='immediate'
                                       )]
                )
            ]
        ),
    ],
    sliders=[
        dict(
            active=0,
            currentvalue=dict(prefix="Timestep: "),
            steps=[dict(method='animate',
                        args=[[f'frame{k}'],
                              dict(mode='immediate',
                                   frame=dict(duration=100, redraw=False),
                                   transition=dict(duration=0)
                                   )
                          ],
                        label=f'{k * iteration_step}'
                        )
                   for k in range(0, int((df.index[-1]+1) / iteration_step))
],
),
]
)


fig = go.Figure(data=data, layout=layout)

fig.update_layout(
    updatemenus=[dict(type='buttons', showactive=False, buttons=[dict(label='Play', method='animate', args=[None, dict(frame=dict(duration=50, redraw=False), fromcurrent=True, transition=dict(duration=0), mode='immediate')]), dict(label='Pause', method='animate', args=[[None], dict(mode='immediate', transition=dict(duration=0), frame=dict(duration=0, redraw=False), mode='immediate')])])])
fig.update_layout(sliders=[dict(active=0, currentvalue=dict(prefix="Timestep: "), steps=[dict(method='animate', args=[[f'frame{k}'], dict(mode='immediate', frame=dict(duration=100, redraw=False), transition=dict(duration=0))], label=f'{k * iteration_step}') for k in range(0, int((df.index[-1]+1) / iteration_step))])])
fig.show()

AttributeError: 'tuple' object has no attribute 'append'

In [16]:
# Dataset
iteration_step = 10000
data=[go.Scatter3d( x=df.loc[::iteration_step, idx[f'{i}', 'x']],
                    y=df.loc[::iteration_step, idx[f'{i}', 'y']],
                    z=df.loc[::iteration_step, idx[f'{i}', 'z']],
                    mode='lines',
                    name=f'Body {i}',
                    line=dict(
                        width=2*df[f'{i}']['mass'][0],
                        colorscale='Viridis'
                        ))
                    for i in range(n_bodies)]

# Layout
zoom = 1.2
axis_range = 10000
layout = go.Layout(
    title='N-Body Simulation',
    autosize=False,
    height=900,
    width=1400,
    template=plotly_template,
    scene=dict(
        aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom),
        xaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        yaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        zaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
    ),
    updatemenus=[dict(type='buttons',
                      showactive=False,
                      buttons=[dict(label='Play',
                                    method='animate',
                                    args=[None, {'frame': {'duration': 100, 'redraw': False}, 'fromcurrent': True, 'mode': 'immediate', 'transition': {'duration': 0}}])])]
)

frames = [go.Frame(data=[go.Scatter3d( x=df.loc[j::iteration_step, idx[f'{i}', 'x']],
                                       y=df.loc[j::iteration_step, idx[f'{i}', 'y']],
                                       z=df.loc[j::iteration_step, idx[f'{i}', 'z']],
                                       mode='lines',
                                       name=f'Body {i}',
                                       line=dict(
                                           width=2*df[f'{i}']['mass'][0],
                                           colorscale='Viridis'
                                       ))
                         for i in range(n_bodies)],
                    name=str(j),
                    layout=layout)
            for j in range(0, len(df), iteration_step)]

fig = go.Figure(data=data, layout=layout, frames=frames)

fig.show()

In [ ]:
import plotly.graph_objs as go
from matplotlib import animation

# extract the x, y, z coordinates of each body so I can animate their 3D plot 
x = df.loc[:,idx[:,'x']].groupby(level=0, axis=1).sum()
y = df.loc[:,idx[:,'y']].groupby(level=0, axis=1).sum()
z = df.loc[:,idx[:,'z']].groupby(level=0, axis=1).sum()


scatter = go.Scatter(x=x.iloc[0, :], y=y.iloc[0, :], mode='markers')
layout = go.Layout(updatemenus=[dict(type='buttons', showactive=False,
                                     buttons=[dict(label='Play',
                                                   method='animate',
                                                   args=[None, {'frame': {'duration': 50, 'redraw': False}, 'fromcurrent': True, 'transition': {'duration': 0}}])])])
fig = go.Figure(data=[scatter], layout=layout)

# Define a function that updates the scatter plot for each frame
def update_scatter(frame):
    scatter.x = x[frame, :]
    scatter.y = y[frame, :]
    return scatter,

# Use the FuncAnimation class to animate the graph
anim = animation.FuncAnimation(fig, update_scatter, frames=10000, interval=50, blit=False)

fig.show()

In [ ]:
print(x.shape)
print(x.iloc[0])

In [ ]:
# print(df[::2])
# print x position for each body every 100 timesteps
# print(df.loc[::100, idx[:, 'x']])
# print x position for body i every 100 timesteps
i=4
print(df.loc[::100, idx[f'{i}', 'x']])

In [ ]:

# Dataset
iteration_step = 100
data=[go.Scatter3d( x=df.loc[::iteration_step, idx[f'{i}', 'x']], # this only retrieves every iteration_step'th row
                    y=df.loc[::iteration_step, idx[f'{i}', 'y']], 
                    z=df.loc[::iteration_step, idx[f'{i}', 'z']],
                    mode='lines',
                    name=f'Body {i}',
                    line=dict(
                        width=2*df[f'{i}']['mass'][0],
                        colorscale='Viridis'
                        ))
                    # line=dict(width=2*df[f'{i}']['mass'][0], color='blue'))
                    for i in range(n_bodies)]


    
# make a slider to go forward and backward in time
steps = []
for i in range(0, total_iterations, iteration_step):
    step = dict(
        method="animate",
        args=[
            [i],
            dict(
                frame=dict(duration=0, redraw=True),
                mode="immediate",
                transition=dict(duration=0),
            ),
        ],
        label=f"{i}",
    )
    steps.append(step)

sliders = [
    dict(
        active=0,
        currentvalue={"prefix": "Iteration: "},
        pad={"t": 50},
        steps=steps,
    )
]

# layout["sliders"] = sliders
# Layout
zoom = 1.2
axis_range = 10000
layout = go.Layout(
    title='N-Body Simulation',
    autosize=False,
    height=900,
    width=1400,
    template=plotly_template,
    updatemenus=[
        dict(
            type="buttons",
            buttons=[
                dict(
                    label="Play",
                    method="animate",
                    args=[
                        None,
                        dict(
                            frame=dict(duration=0, redraw=True),
                            fromcurrent=True,
                            transition=dict(duration=0),
                            mode="immediate",
                        ),
                    ],
                ),
                dict(
                    label="Pause",
                    method="animate",
                    args=[
                        [None],
                        dict(
                            frame=dict(duration=0, redraw=True),
                            mode="immediate",
                            transition=dict(duration=0),
                        ),
                    ],
                ),
            ],
        )
    ],
    sliders=sliders,
    scene=dict(
        aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom),
        xaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        yaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
        zaxis=dict(
            showgrid=False,
            range=[-axis_range, axis_range],
            autorange=False,
        ),
    ),
)

# now make the slider animate the data
# frames = []
# for i in range(0, total_iterations, iteration_step):
#     frame = dict(
#         data=[go.Scatter3d( x=df.loc[i, idx[f'{j}', 'x']], # this only retrieves every iteration_step'th row
#                             y=df.loc[i, idx[f'{j}', 'y']], 
#                             z=df.loc[i, idx[f'{j}', 'z']],
#                             mode='lines',
#                             name=f'Body {j}',
#                             line=dict(
#                                 width=2*df[f'{j}']['mass'][0],
#                                 colorscale='Viridis'
#                                 ))
#                             # line=dict(width=2*df[f'{j}']['mass'][0], color='blue'))
#                             for j in range(n_bodies)],
#         traces=[0, 1, 2, 3, 4, 5, 6, 7, 8, 9],
#         name=f"{i}",
#     )
#     frames.append(frame)

# fig = go.Figure(data=data, layout=layout, frames=frames)


fig = go.Figure(data=data, layout=layout, frames=frames)
# fig.update_layout(template=plotly_template)
# fig.update_layout(yaxis_range=[-1, 1])

# fig.update_layout(

# )

fig.show()

# import plotly.offline as plotoff
# plotoff.plot(fig, filename='nbody.html')
# pio.write_html(fig, file='nbody.html', auto_open=True)

In [ ]:
i=1
xf = df.loc[::iteration_step, idx[f'{i}', 'x']]
# print(xf[,0])
xf.shape
# print first 10 values in xf
print(xf[0:10])

In [ ]:
x_values = []
y_values = []
z_values = []
for i in range(n_bodies):
    x = []
    y = []
    z = []
    for idx in range(0, df.index[-1], iteration_step):
        x.append(df.loc[idx, idx[f'{i}', 'x']])
        y.append(df.loc[idx, idx[f'{i}', 'y']])
        z.append(df.loc[idx, idx[f'{i}', 'z']])
    x_values.append(x)
    y_values.append(y)
    z_values.append(z)

data = [go.Scatter3d(x=x_values[i], y=y_values[i], z=z_values[i]) for i in range(n_bodies)]
updatemenus = [
    dict(
        type='buttons',
        showactive=False,
        buttons=[
            dict(
                label='Next',
                method='update',
                args=[
                    {'x': [x_values[i][idx] for i in range(n_bodies) for idx in range(0, len(x_values[0]), 1)]},
                    {'y': [y_values[i][idx] for i in range(n_bodies) for idx in range(0, len(y_values[0]), 1)]},
                    {'z': [z_values[i][idx] for i in range(n_bodies) for idx in range(0, len(z_values[0]), 1)]}
                ]
            ),
        ]
    )
]
layout = go.Layout(
    scene=dict(
        xaxis_title='X',
        yaxis_title='Y',
        zaxis_title='Z'
    ),
    updatemenus=updatemenus
)

fig = go.Figure(data=data, layout=layout)
fig.show()

In [ ]:
data=[go.Scatter3d( x=df.loc[::iteration_step, idx[f'{i}', 'x']], # this only retrieves every iteration_step'th row
                    y=df.loc[::iteration_step, idx[f'{i}', 'y']], 
                    z=df.loc[::iteration_step, idx[f'{i}', 'z']],
                    mode='lines',
                    name=f'Body {i}',
                    line=dict(
                        width=2*df[f'{i}']['mass'][0],
                        colorscale='Viridis'
                        ))
                    # line=dict(width=2*df[f'{i}']['mass'][0], color='blue'))
                    for i in range(n_bodies)]

updatemenus = [
    dict(
        type='buttons',
        showactive=False,
        buttons=[
            dict(
                label='Next',
                method='update',
                args=[
                    {'x': [df.loc[idx, idx[f'{i}', 'x']] for i in range(n_bodies) for idx in range(0, df.index[-1], iteration_step)]},
                    {'y': [df.loc[idx, idx[f'{i}', 'y']] for i in range(n_bodies) for idx in range(0, df.index[-1], iteration_step)]},
                    {'z': [df.loc[idx, idx[f'{i}', 'z']] for i in range(n_bodies) for idx in range(0, df.index[-1], iteration_step)]}
                ]
            ),
        ]
    )
]

max_x=2000
min_x=-2000
layout = go.Layout(
    title='N-Body Simulation',
    autosize=False,
    height=900,
    width=1400,
    scene=dict(
        aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom)
        ),
    updatemenus=updatemenus,
    template=plotly_template,
    # sliders=[slider],
)                   

fig = go.Figure(data=data, layout=layout)
fig.show()

In [ ]:
# x_data=df.loc[::iteration_step, idx[f'{i}', 'x']]
# y_data=df.loc[::iteration_step, idx[f'{i}', 'y']]
# z_data=df.loc[::iteration_step, idx[f'{i}', 'z']]

data=[go.Scatter3d( x=df.loc[::iteration_step, idx[f'{i}', 'x']], # this only retrieves every iteration_step'th row
                    y=df.loc[::iteration_step, idx[f'{i}', 'y']], 
                    z=df.loc[::iteration_step, idx[f'{i}', 'z']],
                    mode='lines',
                    name=f'Body {i}',
                    line=dict(
                        width=2*df[f'{i}']['mass'][0],
                        colorscale='Viridis'
                        ))
                    # line=dict(width=2*df[f'{i}']['mass'][0], color='blue'))
                    for i in range(n_bodies)]


updatemenus = list([
    dict(
        buttons=list([
            dict(
                args=[{"x": [x_data[0:index] for index in range(0, x_data.index[-1])]}],
                label="X Position",
                method="update"
            ),
            # dict(
            #     args=[{"y": [df.loc[::iteration_step, idx[f'{i}', 'y']] for idx in range(0, df.index[-1], iteration_step)]}],
            #     label="Y Position",
            #     method="update"
            # ),
            # dict(
            #     args=[{"z": [df.loc[::iteration_step, idx[f'{i}', 'z']] for idx in range(0, df.index[-1], iteration_step)]}],
            #     label="Z Position",
            #     method="update"
            # )
        ]),
        direction="down",
        showactive=True,
        type="buttons",
        x=0.1,
        xanchor="left",
        y=1.1,
        yanchor="top"
    ),
])
max_x=2000
min_x=-2000
layout = go.Layout(
    title='N-Body Simulation',
    autosize=False,
    height=900,
    width=1400,
    scene=dict(
        aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom)
        ),
    updatemenus=updatemenus,
    # xaxis=dict(range=[min_x, max_x], autorange=False),
    # yaxis=dict(range=[min_x, max_x], autorange=False),
    # zaxis=dict(range=[min_x, max_x], autorange=False),
    template=plotly_template,
    # sliders=[slider],
)                   

fig = go.Figure(data=data, layout=layout)
# fig.update_layout(template=plotly_template)
fig.show()

In [ ]:
# # Dataset
# data=[go.Scatter3d(x=df[f'{i}']['x'], 
#                     y=df[f'{i}']['y'], 
#                     z=df[f'{i}']['z'],
#                     mode='lines',
#                     name=f'Body {i}',
#                     line=dict(
#                         width=2*df[f'{i}']['mass'][0],
#                         colorscale='Viridis'
#                         ))
#                     # line=dict(width=2*df[f'{i}']['mass'][0], color='blue'))
#                     for i in range(n_bodies)]

# # Layout
# zoom = 1.2

# layout = go.Layout(
#     title='N-Body Simulation',
#     autosize=False,
#     height=900,
#     width=1400,
#     scene=dict(
#         aspectratio=go.layout.scene.Aspectratio(x=zoom, y=zoom, z=zoom)
#         ),
# )
    
# fig = go.Figure(data=data, layout=layout)
# fig.update_layout(template=plotly_template)
# fig.show()

